![Logo 1](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech1.jpg)
<div class="alert alert-block alert-info">
<h1> Modelowanie Języka</h1>
<h2> 14. <i>Model rekurencyjny z atencją</i>  [ćwiczenia]</h2> 
<h3> Jakub Pokrywka (2022)</h3>
</div>

![Logo 2](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech2.jpg)

notebook na podstawie:

# https://pytorch.org/tutorials/intermediate/seq2seq_translation_tutorial.html

In [1]:
from __future__ import unicode_literals, print_function, division
from io import open
import unicodedata
import string
import re
import random

import torch
import torch.nn as nn
from torch import optim
import torch.nn.functional as F

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

In [2]:
SOS_token = 0
EOS_token = 1

class Lang:
    def __init__(self):
        self.word2index = {}
        self.word2count = {}
        self.index2word = {0: "SOS", 1: "EOS"}
        self.n_words = 2  # Count SOS and EOS

    def addSentence(self, sentence):
        for word in sentence.split(' '):
            self.addWord(word)

    def addWord(self, word):
        if word not in self.word2index:
            self.word2index[word] = self.n_words
            self.word2count[word] = 1
            self.index2word[self.n_words] = word
            self.n_words += 1
        else:
            self.word2count[word] += 1

In [3]:
pairs = []
with open('data/eng-pol.txt') as f:
    for line in f:
        eng_line, pol_line = line.lower().rstrip().split('\t')

        eng_line = re.sub(r"([.!?])", r" \1", eng_line)
        eng_line = re.sub(r"[^a-zA-Z.!?]+", r" ", eng_line)

        pol_line = re.sub(r"([.!?])", r" \1", pol_line)
        pol_line = re.sub(r"[^a-zA-Z.!?ąćęłńóśźżĄĆĘŁŃÓŚŹŻ]+", r" ", pol_line)

        pairs.append([eng_line, pol_line])




In [4]:
pairs[1]

['hi .', 'cześć .']

In [5]:
MAX_LENGTH = 10
eng_prefixes = (
    "i am ", "i m ",
    "he is", "he s ",
    "she is", "she s ",
    "you are", "you re ",
    "we are", "we re ",
    "they are", "they re "
)

pairs = [p for p in pairs if len(p[0].split(' ')) < MAX_LENGTH and len(p[1].split(' ')) < MAX_LENGTH]
pairs = [p for p in pairs if p[0].startswith(eng_prefixes)]

eng_lang = Lang()
pol_lang = Lang()

for pair in pairs:
    eng_lang.addSentence(pair[0])
    pol_lang.addSentence(pair[1])

In [6]:
pairs[0]

['i m ok .', 'ze mną wszystko w porządku .']

In [7]:
pairs[1]

['i m up .', 'wstałem .']

In [8]:
pairs[2]

['i m tom .', 'jestem tom .']

In [9]:
eng_lang.n_words

1828

In [10]:
pol_lang.n_words

2883

In [11]:
class EncoderRNN(nn.Module):
    def __init__(self, input_size, embedding_size, hidden_size):
        super(EncoderRNN, self).__init__()
        self.embedding_size = 200
        self.hidden_size = hidden_size

        self.embedding = nn.Embedding(input_size, self.embedding_size)
        self.gru = nn.GRU(self.embedding_size, hidden_size)

    def forward(self, input, hidden):
        embedded = self.embedding(input).view(1, 1, -1)
        output = embedded
        output, hidden = self.gru(output, hidden)
        return output, hidden

    def initHidden(self):
        return torch.zeros(1, 1, self.hidden_size, device=device)

In [12]:
class DecoderRNN(nn.Module):
    def __init__(self, embedding_size, hidden_size, output_size):
        super(DecoderRNN, self).__init__()
        self.embedding_size = embedding_size
        self.hidden_size = hidden_size

        self.embedding = nn.Embedding(output_size, self.embedding_size)
        self.gru = nn.GRU(self.embedding_size, hidden_size)
        self.out = nn.Linear(hidden_size, output_size)
        self.softmax = nn.LogSoftmax(dim=1)

    def forward(self, input, hidden):
        output = self.embedding(input).view(1, 1, -1)
        output = F.relu(output)
        output, hidden = self.gru(output, hidden)
        output = self.softmax(self.out(output[0]))
        return output, hidden

    def initHidden(self):
        return torch.zeros(1, 1, self.hidden_size, device=device)

In [13]:
class AttnDecoderRNN(nn.Module):
    def __init__(self, embedding_size, hidden_size, output_size, dropout_p=0.1, max_length=MAX_LENGTH):
        super(AttnDecoderRNN, self).__init__()
        self.embedding_size = embedding_size
        self.hidden_size = hidden_size
        self.output_size = output_size
        self.dropout_p = dropout_p
        self.max_length = max_length

        self.embedding = nn.Embedding(self.output_size, self.embedding_size)
        self.attn = nn.Linear(self.hidden_size + self.embedding_size, self.max_length)
        self.attn_combine = nn.Linear(self.hidden_size + self.embedding_size, self.embedding_size)
        self.dropout = nn.Dropout(self.dropout_p)
        self.gru = nn.GRU(self.embedding_size, self.hidden_size)
        self.out = nn.Linear(self.hidden_size, self.output_size)

    def forward(self, input, hidden, encoder_outputs):
        embedded = self.embedding(input).view(1, 1, -1)
        embedded = self.dropout(embedded)

        attn_weights = F.softmax(
            self.attn(torch.cat((embedded[0], hidden[0]), 1)), dim=1)
        attn_applied = torch.bmm(attn_weights.unsqueeze(0),
                                 encoder_outputs.unsqueeze(0))
        import pdb; pdb.set_trace()

        output = torch.cat((embedded[0], attn_applied[0]), 1)
        output = self.attn_combine(output).unsqueeze(0)

        output = F.relu(output)
        output, hidden = self.gru(output, hidden)

        output = F.log_softmax(self.out(output[0]), dim=1)
        return output, hidden, attn_weights

    def initHidden(self):
        return torch.zeros(1, 1, self.hidden_size, device=device)

In [14]:
def tensorFromSentence(sentence, lang):
    indexes = [lang.word2index[word] for word in sentence.split(' ')]
    indexes.append(EOS_token)
    return torch.tensor(indexes, dtype=torch.long, device=device).view(-1, 1)


In [15]:
teacher_forcing_ratio = 0.5

def train_one_batch(input_tensor, target_tensor, encoder, decoder, optimizer, criterion, max_length=MAX_LENGTH):
    encoder_hidden = encoder.initHidden()


    optimizer.zero_grad()

    input_length = input_tensor.size(0)
    target_length = target_tensor.size(0)

    encoder_outputs = torch.zeros(max_length, encoder.hidden_size, device=device)

    loss = 0

    for ei in range(input_length):
        encoder_output, encoder_hidden = encoder(input_tensor[ei], encoder_hidden)
        encoder_outputs[ei] = encoder_output[0, 0]

    decoder_input = torch.tensor([[SOS_token]], device=device)

    decoder_hidden = encoder_hidden

    use_teacher_forcing = True if random.random() < teacher_forcing_ratio else False

    if use_teacher_forcing:
        for di in range(target_length):
            decoder_output, decoder_hidden, decoder_attention = decoder(decoder_input, decoder_hidden, encoder_outputs)
            loss += criterion(decoder_output, target_tensor[di])
            decoder_input = target_tensor[di]  # Teacher forcing

    else:
        for di in range(target_length):
            decoder_output, decoder_hidden, decoder_attention = decoder(decoder_input, decoder_hidden, encoder_outputs)
            topv, topi = decoder_output.topk(1)
            decoder_input = topi.squeeze().detach()  # detach from history as input

            loss += criterion(decoder_output, target_tensor[di])
            if decoder_input.item() == EOS_token:
                break

    loss.backward()

    optimizer.step()

    return loss.item() / target_length

In [16]:
def trainIters(encoder, decoder, n_iters, print_every=1000, learning_rate=0.01):
    print_loss_total = 0  # Reset every print_every
    encoder.train()
    decoder.train()

    optimizer = optim.SGD(list(encoder.parameters()) + list(decoder.parameters()), lr=learning_rate)
    
    training_pairs = [random.choice(pairs) for _ in range(n_iters)]
    training_pairs = [(tensorFromSentence(p[0], eng_lang), tensorFromSentence(p[1], pol_lang)) for p in training_pairs]
    
    criterion = nn.NLLLoss()

    for i in range(1, n_iters + 1):
        training_pair = training_pairs[i - 1]
        input_tensor = training_pair[0]
        target_tensor = training_pair[1]

        loss = train_one_batch(input_tensor,
                               target_tensor,
                               encoder,
                               decoder,
                               optimizer,

                               criterion)
        
        print_loss_total += loss

        if i % print_every == 0:
            print_loss_avg = print_loss_total / print_every
            print_loss_total = 0
            print(f'iter: {i}, loss: {print_loss_avg}')


In [17]:
def evaluate(encoder, decoder, sentence, max_length=MAX_LENGTH):
    encoder.eval()
    decoder.eval()
    with torch.no_grad():
        input_tensor = tensorFromSentence(sentence, eng_lang)
        input_length = input_tensor.size()[0]
        encoder_hidden = encoder.initHidden()

        encoder_outputs = torch.zeros(max_length, encoder.hidden_size, device=device)

        for ei in range(input_length):
            encoder_output, encoder_hidden = encoder(input_tensor[ei], encoder_hidden)
            encoder_outputs[ei] += encoder_output[0, 0]

        decoder_input = torch.tensor([[SOS_token]], device=device)

        decoder_hidden = encoder_hidden

        decoded_words = []
        decoder_attentions = torch.zeros(max_length, max_length)

        for di in range(max_length):
            decoder_output, decoder_hidden, decoder_attention = decoder(
                decoder_input, decoder_hidden, encoder_outputs)
            decoder_attentions[di] = decoder_attention.data
            topv, topi = decoder_output.data.topk(1)
            if topi.item() == EOS_token:
                decoded_words.append('<EOS>')
                break
            else:
                decoded_words.append(pol_lang.index2word[topi.item()])

            decoder_input = topi.squeeze().detach()

        return decoded_words, decoder_attentions[:di + 1]

In [18]:
def evaluateRandomly(encoder, decoder, n=10):
    for i in range(n):
        pair = random.choice(pairs)
        print('>', pair[0])
        print('=', pair[1])
        output_words, attentions = evaluate(encoder, decoder, pair[0])
        output_sentence = ' '.join(output_words)
        print('<', output_sentence)
        print('')

In [19]:
embedding_size = 200
hidden_size = 256
encoder1 = EncoderRNN(eng_lang.n_words, embedding_size, hidden_size).to(device)
attn_decoder1 = AttnDecoderRNN(embedding_size, hidden_size, pol_lang.n_words, dropout_p=0.1).to(device)

In [ ]:
trainIters(encoder1, attn_decoder1, 10_000, print_every=50)

> /tmp/ipykernel_41821/2519748186.py(27)forward()
     25         import pdb; pdb.set_trace()
     26 
---> 27         output = torch.cat((embedded[0], attn_applied[0]), 1)
     28         output = self.attn_combine(output).unsqueeze(0)
     29 

ipdb> embedded
tensor([[[-0.7259,  0.0000,  2.2112,  1.1947, -0.1261, -1.0427, -1.4295,
           0.1567, -0.3949, -1.0815,  1.1206,  2.0630,  2.8148, -1.8538,
          -1.5486, -0.4900, -0.0000,  0.0000, -1.5046,  2.0329, -0.5872,
           1.5764, -0.0000,  1.1447, -0.4200, -0.1560,  0.1723,  1.5950,
           1.2955, -0.5796, -0.0000, -0.8989,  0.4737,  1.7037,  0.8787,
          -0.2064,  1.9589,  2.0400, -1.0883,  1.0515,  0.0540,  0.1436,
           1.2383,  0.4912, -1.7719,  1.6435,  1.5523,  2.3576,  0.0000,
           0.4063, -0.0821, -1.2872,  0.8372, -0.5638,  0.0706,  0.4151,
          -0.0000,  1.1651,  1.7333, -0.1684, -0.0000, -0.8560, -0.0000,
           2.7717, -0.4485, -0.8488,  0.8165,  2.1787, -1.0720, -0.3146,
        

ipdb> attn_weights.shape
torch.Size([1, 10])
ipdb> encoder_outputs.shape
torch.Size([10, 256])
ipdb> embedded.shape
torch.Size([1, 1, 200])
ipdb> attn_applied.shape
torch.Size([1, 1, 256])
ipdb>  output = torch.cat((embedded[0], attn_applied[0]), 1)
ipdb> output.shape
torch.Size([1, 456])
ipdb> output = self.attn_combine(output).unsqueeze(0)
ipdb> output.shape
torch.Size([1, 1, 200])
ipdb> attn_weights
tensor([[0.0817, 0.1095, 0.1425, 0.1611, 0.0574, 0.0546, 0.0374, 0.0621, 0.0703,
         0.2234]], grad_fn=<SoftmaxBackward0>)
ipdb> attn_weights.shape
torch.Size([1, 10])
ipdb> attn_applied.shape
torch.Size([1, 1, 256])
ipdb> attn_applied.shape
torch.Size([1, 1, 256])
ipdb> attn_applied
tensor([[[ 0.0354, -0.0156, -0.0048, -0.0936,  0.0637,  0.1516,  0.1419,
           0.1106,  0.0511,  0.0235, -0.0622,  0.0725,  0.0709, -0.0624,
           0.1407, -0.0069, -0.1602, -0.1883, -0.1707, -0.1528, -0.0296,
          -0.0500,  0.2115,  0.0705, -0.1385, -0.0487, -0.0165, -0.0128,
          -0

ipdb> torch.cat((embedded[0], attn_applied[0]), 1).shape
torch.Size([1, 456])
ipdb> attnn_weights
*** NameError: name 'attnn_weights' is not defined
ipdb> attn_weights.shape
torch.Size([1, 10])
ipdb> attn_applied
tensor([[[ 0.0354, -0.0156, -0.0048, -0.0936,  0.0637,  0.1516,  0.1419,
           0.1106,  0.0511,  0.0235, -0.0622,  0.0725,  0.0709, -0.0624,
           0.1407, -0.0069, -0.1602, -0.1883, -0.1707, -0.1528, -0.0296,
          -0.0500,  0.2115,  0.0705, -0.1385, -0.0487, -0.0165, -0.0128,
          -0.0594,  0.0209, -0.1081,  0.0509,  0.0655,  0.1314, -0.0455,
          -0.0049, -0.1527, -0.1900, -0.0019,  0.0295, -0.0308,  0.0886,
           0.1369, -0.1571,  0.0518, -0.0991, -0.0310, -0.1781, -0.0290,
           0.0558,  0.0585, -0.1045, -0.0027, -0.0476, -0.0377, -0.1026,
           0.0481,  0.0398, -0.0956,  0.0655, -0.1449,  0.0193, -0.0380,
           0.0401,  0.0491, -0.1925,  0.0669,  0.0774,  0.0604,  0.1187,
          -0.0401,  0.1094,  0.0706,  0.0474,  0.0178, -0

In [ ]:
evaluateRandomly(encoder1, attn_decoder1)

In [ ]:
## ZADANIE

Gonito "WMT2017 Czech-English machine translation challenge for news "

Proszę wytrenować najpierw model german -> english, a później dotrenować na czech-> english.
Można wziąć inicjalizować enkoder od nowa lub nie. Proszę w każdym razie użyć wytrenowanego dekodera.